In [1]:
import pandas as pd
import numpy  as np
import re                              # Used for splitting the Items with multiple delimiters
from   collections import Counter      # To count items in dictionaries
from   itertools   import combinations # To generate combinations of items
from   itertools   import permutations # To generate permutations of items
import functools
from collections import defaultdict  

routeID        = -1 # initialized to -1 in order to force the first execution to the "else"
orderID        = -1
tmp = [None] * 15

# The dataset was created with the notebook "DatasetCreation.ipynb".

routes = pd.read_csv('route_trips.csv', 
                     delimiter = ',', 
                     encoding  = 'utf-8')

routes.drop(routes.columns[0], 
            axis    = 1, 
            inplace = True)

In [2]:
# Prepare the delimiters for splitting the items
delimiters   = ",", "{", "}", "'"
regexPattern = '|'.join(map(re.escape, delimiters))

In [3]:
# Produce a new column for the Items
newItemsColumn = []
for index in range(0, len(routes)):
    tmp = list(filter(None, re.split(regexPattern, routes.Items[index])))
    newItemsColumn.append([item for item in tmp 
                                   if item.strip()])
routes.Items = newItemsColumn

In [4]:
# Save in a dictionary the number of trip for each order 
routeDimension = defaultdict(list)
for route in routes.RouteId:
    routeDimension[route] = max([order for order in routes[routes.RouteId == route].Order]) + 1

In [5]:
# Set the threshold for the support of Frequent itemset theory
supportThreshold = 5

items   = [item for items in routes.Items 
                   for item in items]

# Count the occurrencies of each item in the whole dataset
# ("items" now contains a list of all the products for each trip)
itemCount = Counter([(item,) for item in items])
support = itemCount

# Select only those items that appear more than the support
frequentItems = [item for item in itemCount 
                    if itemCount[item] >= supportThreshold]

In [6]:
routes.Items

0      [Sardines-in-brine, Cauliflower-cheese, Mayona...
1      [Kombucha, Mango-drink, Mayonaise, Bouillonter...
2      [Ale, Burrito-kit, Mayonaise, Dindes, Senate-b...
3      [Miels, Dolminades, Ale, Yaourts-aux-fruits, C...
4      [Fuet-met-zwarte-peper, Kase, Beef-broth, Yaou...
5      [Corn-snacks, Indian-food-mixes, Pousses-de-ba...
6      [Corn-snacks, Indian-food-mixes, Chili-con-car...
7      [Corn-snacks, Indian-food-mixes, Ghee, San-cho...
8      [Corn-snacks, Fruits-frais, Frozen-peas, Ghee,...
9      [Corn-snacks, Cardamom-pods, Cigarettes, Garli...
10     [Corn-snacks, Microwave-popcorn, Cigarettes, C...
11     [Fromages, Fresh-juices, Creme-chocolat, Iced-...
12     [Ale, Bonbons-au-chocolat, Fresh-juices, Pates...
13     [Sparkling-water-beverage, Formulated-suppleme...
14     [Peanut-butter-and-chocolat-chip-cereal-bar, F...
15     [Peanut-butter-and-chocolat-chip-cereal-bar, C...
16     [Chocolate-coins, Lime-marmalades, Turkish-fer...
17     [Christmas-food, Guava-j

In [7]:
[f for ft in frequentItems for f in ft]

['Sardines-in-brine',
 'Mayonaise',
 'Cornichons',
 'Dindes',
 'Blackcurrent-juice-drink',
 'White-peaches',
 'Earl-grey',
 'Kiwi-fruit',
 'Danette-chocolate-dessert',
 'Kombucha',
 'Mango-drink',
 'Sucres',
 'Venison-burger',
 'Fromage-a-pate-dure',
 'Camembert-cheese',
 'Burrito-kit',
 'Senate-bean-soup',
 'Rice-wine',
 'Linsen',
 'Eau-de-vie',
 'Butter-shortbread-fingers',
 'Frozen-dumpling',
 'Miels',
 'Dolminades',
 'Yaourts-aux-fruits',
 'Chicken-eggs',
 'Grape-juice-drink',
 'Fruchtschnitte',
 'Ciabatta',
 'Still-water',
 'Frozen-petits-pois',
 'Kase',
 'Creme-chocolat',
 'Peach-drink',
 'Gnocchi',
 'Tabbouleh',
 'Lime-marmalades',
 'Corn-snacks',
 'Indian-food-mixes',
 'Pousses-de-bambou',
 'Snacks',
 'Slaty-snack',
 'Chocolats-blancs',
 'Hawaiian-sweet-rolls',
 'Chili-con-carne',
 'Turkish-delight',
 'Fresh-bread',
 'Meat-paste',
 'Tartar-sauce',
 'Stuffing',
 'Tabouleh-salad',
 'Ghee',
 'San-choy-bao',
 'Dark-chocolate-block',
 'Fizzy-drinks',
 'Faux-fromage',
 'Blueberry-syr

In [8]:
# Now we remove from the Items those that are not frequentItems
routes.Items = [list(filter(lambda i: i in [f for ft in frequentItems for f in ft], items)) for items in routes.Items]

In [9]:
routes.Items

0      [Sardines-in-brine, Mayonaise, Cornichons, Din...
1      [Kombucha, Mango-drink, Mayonaise, Dindes, Bla...
2      [Burrito-kit, Mayonaise, Dindes, Senate-bean-s...
3      [Miels, Dolminades, Yaourts-aux-fruits, Chicke...
4      [Kase, Yaourts-aux-fruits, Grape-juice-drink, ...
5      [Corn-snacks, Indian-food-mixes, Pousses-de-ba...
6      [Corn-snacks, Indian-food-mixes, Chili-con-car...
7      [Corn-snacks, Indian-food-mixes, Ghee, San-cho...
8      [Corn-snacks, Fruits-frais, Frozen-peas, Ghee,...
9      [Corn-snacks, Cardamom-pods, Cigarettes, Garli...
10     [Corn-snacks, Microwave-popcorn, Cigarettes, C...
11     [Fromages, Fresh-juices, Creme-chocolat, Iced-...
12     [Bonbons-au-chocolat, Fresh-juices, Pates-frai...
13     [Sparkling-water-beverage, Formulated-suppleme...
14     [Peanut-butter-and-chocolat-chip-cereal-bar, F...
15     [Peanut-butter-and-chocolat-chip-cereal-bar, C...
16     [Chocolate-coins, Lime-marmalades, Turkish-fer...
17     [Guava-juice, Taco-shell

In [10]:
# Here we generate combinations of 2 frequent items 
# and we count how many pairs there are for each combination
pairCount     = Counter([comb for combs in [list(permutations(items, 2)) for items in routes.Items] 
                                 for comb in combs])
support = support + pairCount

# and select only those that appear more than the support
frequentPairs = [comb for comb in pairCount 
                         if pairCount[comb] >= supportThreshold]

In [11]:
# then sort them for next operations and reduce them to a set for removing duplicates  
frequentPairs = list(set( [ tuple(fp) for fp in [sorted(fp) for fp in frequentPairs ] ] ) )

In [12]:
# Here we remove the duplicates from the frequentPairs
itemInPairs = set(f for fp in frequentPairs for f in fp)

In [13]:
# This is used to keep track of the tuples at the i-th step
itemsithStep = [list(filter(lambda i: i in itemInPairs, items)) for items in routes.Items]

In [14]:
#def Remove(duplicate): 
#    final_list = [] 
#    for num in duplicate: 
#        if num not in final_list: 
#            final_list.append(num) 
#    return final_list 

In [ ]:
# Max depth for frequent tuples
#depth = 6
#frequentTuples = []
#for i in range(2,depth):
#    subset = []
#    for sl in range(0,len(frequentPairs)):
#        tryitems = frequentPairs[sl][:-1]
#        possibleitems = []
#        for asl in frequentPairs[:sl]+frequentPairs[sl+1:]:
#            if (len(set(tryitems).intersection(set(asl))) == len(tryitems)):
#                possibleitems.append(list(set(asl).difference(set(tryitems))))
#        if possibleitems != []:
#            for ssl in list(combinations(frequentPairs[sl], len(frequentPairs[sl])-1)):
#                if ssl != tryitems:
#                    for el in possibleitems:
#                        elem = el
#                        elem.extend(ssl)
#                        c = tuple(set(elem))
#                        if(set(c) in [set(fp) for fp in frequentPairs]):
#                            c = list(c)
#                            c.extend(list(item for item in tryitems))
#                            subset.append(tuple(set(c)))
#    subset = [tuple(s) for s in Remove(list(set(sb) for sb in subset))]
#    combination = [list(combinations(items, i+1)) for items in routes.Items]
#    comb = [tuple(comb) for combs in combination 
#                for comb in combs]
#    tuplesCount = Counter(comb)
    # and select only those that appear more than the support
#    frequentT = [tuples for tuples in tuplesCount 
#                        if tuplesCount[tuples] >= support]
#    frequentTuples.append(frequentT)
#    frequentPairs = frequentT

In [15]:
# Max depth for frequent tuples
depth            = 6
frequentTuples   = []
for i in range(2, depth):
    subset       = []
    combination  = [list(permutations(items, i + 1)) for items in itemsithStep]
    comb         = [tuple(comb) for combs in combination 
                                   for comb in combs]
    tuplesCount  = Counter(comb)
    support = support + tuplesCount
    frequentT    = [tuples for tuples in tuplesCount 
                            if tuplesCount[tuples] >= supportThreshold]
    frequentTuples.append(frequentT)
    itemInTuples = set(f for fp in frequentT for f in fp)
    itemsithStep = [list(filter(lambda i: i in itemInTuples, items)) for items in itemsithStep]

In [16]:
# popularTuples will be our container for interesting objects. 
# Now we can find inside popular items and popular pairs but it is going to be extended.
popularTuples = [ft for ft in frequentItems]
popularTuples.extend(frequentPairs)
for ft in frequentTuples:
    popularTuples.extend(ft)

In [17]:
def matches(rid, order, popularTuples):
    itemList   = []
    orderItems = routes.Items[(routes.RouteId == rid) & 
                              (routes.Order   == order)
                             ].tolist()[0]
    for obj in popularTuples:
        check = True # here we check if none of the object is inside the orderItems
        for item in obj:
            if item not in orderItems:
                check = False
                break
        if check:    # in that case we add it to the itemList
            itemList.append(list(obj))
    return itemList

def anyOrder(rid, oid, start, popularTuples):
    global orderID
    global tmp
    t = []
    if tmp[oid] == None:
        t = matches(rid, oid, popularTuples)
        tmp[oid] = t
    else:
        t = tmp[oid]
    
    return tuple([oid - start - 1, t])
    
def divideOrder(rid, order, popularTuples):
    global orderID
    global routeID
    global tmp
    dim = routeDimension[rid]
    if (order + 1 < dim):
        if(rid != routeID):
            routeID = rid
            orderID = order
            tmp = [None] * 15
        return [anyOrder(rid, oid, order, popularTuples) for oid in range(order + 1, dim)]
    else:
        return [(-1, [])]

def searchNext(tuples, popularTuples):
    keys        = [(routes.RouteId[row], routes.Order[row]) 
                 for row in range(0, len(routes)) 
                     if set(tuples).intersection(set(routes.Items[row])) == set(tuples)]
    newTuples   = [divideOrder(key[0], key[1], popularTuples) for key in keys]
    return newTuples

In [18]:
popularPatterns = [(pop, searchNext(pop, popularTuples)) for pop in popularTuples]

84.12956976890564


In [19]:
# Confidence and Interest level
confidence = 0.5
interest = 0.5

def patternSum(pattern):
    finalPattern = [(i, sum(val for val in pattern[i])) for i in pattern]
    return finalPattern
        
def patternReduce(pattern):
    d = defaultdict(list)
    for key, value in pattern:
        t = tuple([key[0], tuple(key[1])])
        d[t].append(value)
    return d

def patternCount(pattern):
    reduction = patternReduce(pattern)
    count = patternSum(reduction)
    return count

# Limit of classification for frequent Patterns
def patternExtraction(pattern, limit = 5):
    patternLevel = [[(x[0], y), 1] for pat in pattern[1] for x in pat for y in x[1]]
    patternLevel = patternCount(patternLevel)
    finalPattern = [pat for pat in patternLevel if ((pat[1]/support[pattern[0]]) >= confidence) &
                                                   (abs((pat[1]/support[pattern[0]] -
                                                      (support[pat[0][1]]/len(routes)))) >= interest)] 
    return (pattern[0], finalPattern)

In [20]:
patterns = [patternExtraction(pattern) for pattern in popularPatterns]

In [21]:
patterns

[(('Sardines-in-brine',),
  [((0, ('Asian-sauces',)), 4),
   ((1, ('Raw',)), 4),
   ((1, ('Yellow-peaches',)), 4),
   ((2, ('Organic-and-premium-pepper-cambodia',)), 4),
   ((2, ('Raw',)), 4),
   ((2, ('Organic-and-premium-pepper-cambodia', 'Raw')), 4),
   ((3, ('Organic-and-premium-pepper-cambodia',)), 4),
   ((3, ('Raw',)), 4),
   ((3, ('Organic-and-premium-pepper-cambodia', 'Raw')), 4)]),
 (('Mayonaise',), []),
 (('Cornichons',), []),
 (('Dindes',), []),
 (('Blackcurrent-juice-drink',), []),
 (('White-peaches',), []),
 (('Earl-grey',), []),
 (('Kiwi-fruit',), []),
 (('Danette-chocolate-dessert',), []),
 (('Kombucha',), []),
 (('Mango-drink',), []),
 (('Sucres',), []),
 (('Venison-burger',), []),
 (('Fromage-a-pate-dure',), [((0, ('Fromage-a-pate-dure',)), 11)]),
 (('Camembert-cheese',), []),
 (('Burrito-kit',), []),
 (('Senate-bean-soup',), []),
 (('Rice-wine',), []),
 (('Linsen',), []),
 (('Eau-de-vie',), []),
 (('Butter-shortbread-fingers',), []),
 (('Frozen-dumpling',), []),
 (('

In [22]:
#stampo solo quelli che poi hanno dei livelli oltre all'elemento corrente
for p in patterns:
    c = 0
    if p[1] != []:
        print("-> ", p[0][0])
        for item in p[1]:
            s = "\t"
            if item != []:
                p = ""
                for i in range(0, item[0][0]):
                    s += "\t"
                for k in range(0,len(item[0][1])):
                    if k == (len(item[0][1])-1):
                        p += "\t"+item[0][1][k]
                    else:
                        p += "\t"+item[0][1][k] + ","
                print(s, item[0][0],"->", p)
        print()

->  Sardines-in-brine
	 0 -> 	Asian-sauces
		 1 -> 	Raw
		 1 -> 	Yellow-peaches
			 2 -> 	Organic-and-premium-pepper-cambodia
			 2 -> 	Raw
			 2 -> 	Organic-and-premium-pepper-cambodia,	Raw
				 3 -> 	Organic-and-premium-pepper-cambodia
				 3 -> 	Raw
				 3 -> 	Organic-and-premium-pepper-cambodia,	Raw

->  Fromage-a-pate-dure
	 0 -> 	Fromage-a-pate-dure

->  Lime-marmalades
	 0 -> 	Lime-marmalades

->  Corn-snacks
	 0 -> 	Corn-snacks

->  Tabouleh-salad
	 0 -> 	Corn-snacks
		 1 -> 	Corn-snacks

->  Ghee
	 0 -> 	Ghee

->  Faux-fromage
	 0 -> 	Faux-fromage

->  Peach-juice-drink
	 0 -> 	Peach-juice-drink
	 0 -> 	Frozen-vegetable-mix
	 0 -> 	Frozen-vegetable-mix,	Peach-juice-drink

->  Fruits-en-conserve
	 0 -> 	Fruits-en-conserve

->  Fruit-buns
	 0 -> 	Fruit-buns

->  Cigarettes
	 0 -> 	Cigarettes

->  Chocolate-coins
	 0 -> 	Turkish-fermented-drink
		 1 -> 	Turkish-fermented-drink
		 1 -> 	Frozen-pork-buns
			 2 -> 	Frozen-pork-buns

->  Turkish-fermented-drink
	 0 -> 	Turkish-fermen

		 1 -> 	Cherry-juice,	Soup-mixes,	Fruit-buns,	Power-drink,	Fresh-garlic
		 1 -> 	Cherry-juice,	Soup-mixes,	Fresh-garlic,	Fruit-buns,	Power-drink
		 1 -> 	Cherry-juice,	Soup-mixes,	Fresh-garlic,	Power-drink,	Fruit-buns
		 1 -> 	Cherry-juice,	Soup-mixes,	Power-drink,	Fruit-buns,	Fresh-garlic
		 1 -> 	Cherry-juice,	Soup-mixes,	Power-drink,	Fresh-garlic,	Fruit-buns
		 1 -> 	Cherry-juice,	Fresh-garlic,	Fruit-buns,	Soup-mixes,	Power-drink
		 1 -> 	Cherry-juice,	Fresh-garlic,	Fruit-buns,	Power-drink,	Soup-mixes
		 1 -> 	Cherry-juice,	Fresh-garlic,	Soup-mixes,	Fruit-buns,	Power-drink
		 1 -> 	Cherry-juice,	Fresh-garlic,	Soup-mixes,	Power-drink,	Fruit-buns
		 1 -> 	Cherry-juice,	Fresh-garlic,	Power-drink,	Fruit-buns,	Soup-mixes
		 1 -> 	Cherry-juice,	Fresh-garlic,	Power-drink,	Soup-mixes,	Fruit-buns
		 1 -> 	Cherry-juice,	Power-drink,	Fruit-buns,	Soup-mixes,	Fresh-garlic
		 1 -> 	Cherry-juice,	Power-drink,	Fruit-buns,	Fresh-garlic,	Soup-mixes
		 1 -> 	Cherry-juice,	Power-drink,	Soup-mixes,	Fru

	 0 -> 	Lemongrass-paste,	Sussungsmittel,	Instant-porridge,	Chicken-kievs,	Polenta
	 0 -> 	Lemongrass-paste,	Sussungsmittel,	Instant-porridge,	Polenta,	Chicken-kievs
	 0 -> 	Lemongrass-paste,	Sussungsmittel,	Polenta,	Chicken-kievs,	Instant-porridge
	 0 -> 	Lemongrass-paste,	Sussungsmittel,	Polenta,	Instant-porridge,	Chicken-kievs
	 0 -> 	Chicken-kievs,	Lemongrass-paste,	Instant-porridge,	Polenta,	Sussungsmittel
	 0 -> 	Chicken-kievs,	Lemongrass-paste,	Instant-porridge,	Sussungsmittel,	Polenta
	 0 -> 	Chicken-kievs,	Lemongrass-paste,	Polenta,	Instant-porridge,	Sussungsmittel
	 0 -> 	Chicken-kievs,	Lemongrass-paste,	Polenta,	Sussungsmittel,	Instant-porridge
	 0 -> 	Chicken-kievs,	Lemongrass-paste,	Sussungsmittel,	Instant-porridge,	Polenta
	 0 -> 	Chicken-kievs,	Lemongrass-paste,	Sussungsmittel,	Polenta,	Instant-porridge
	 0 -> 	Chicken-kievs,	Instant-porridge,	Lemongrass-paste,	Polenta,	Sussungsmittel
	 0 -> 	Chicken-kievs,	Instant-porridge,	Lemongrass-paste,	Sussungsmittel,	Polenta
	 0 

	 0 -> 	Soup-mixes,	Fresh-garlic,	Fruit-buns
	 0 -> 	Soup-mixes,	Fresh-garlic,	Power-drink
	 0 -> 	Soup-mixes,	Power-drink,	Cherry-juice
	 0 -> 	Soup-mixes,	Power-drink,	Fruit-buns
	 0 -> 	Soup-mixes,	Power-drink,	Fresh-garlic
	 0 -> 	Fresh-garlic,	Cherry-juice,	Fruit-buns
	 0 -> 	Fresh-garlic,	Cherry-juice,	Soup-mixes
	 0 -> 	Fresh-garlic,	Cherry-juice,	Power-drink
	 0 -> 	Fresh-garlic,	Fruit-buns,	Cherry-juice
	 0 -> 	Fresh-garlic,	Fruit-buns,	Soup-mixes
	 0 -> 	Fresh-garlic,	Fruit-buns,	Power-drink
	 0 -> 	Fresh-garlic,	Soup-mixes,	Cherry-juice
	 0 -> 	Fresh-garlic,	Soup-mixes,	Fruit-buns
	 0 -> 	Fresh-garlic,	Soup-mixes,	Power-drink
	 0 -> 	Fresh-garlic,	Power-drink,	Cherry-juice
	 0 -> 	Fresh-garlic,	Power-drink,	Fruit-buns
	 0 -> 	Fresh-garlic,	Power-drink,	Soup-mixes
	 0 -> 	Power-drink,	Cherry-juice,	Fruit-buns
	 0 -> 	Power-drink,	Cherry-juice,	Soup-mixes
	 0 -> 	Power-drink,	Cherry-juice,	Fresh-garlic
	 0 -> 	Power-drink,	Fruit-buns,	Cherry-juice
	 0 -> 	Power-drink,	Fruit-bu


->  Brussels-pate
	 0 -> 	Brussels-pate

->  Coconut-creams
	 0 -> 	Pure-cod-liver-oil
	 0 -> 	Hot-fudge
	 0 -> 	Coconut-creams
	 0 -> 	Coconut-creams,	Hot-fudge
	 0 -> 	Coconut-creams,	Pure-cod-liver-oil
	 0 -> 	Hot-fudge,	Pure-cod-liver-oil
	 0 -> 	Hot-fudge,	Pure-cod-liver-oil,	Coconut-creams
	 0 -> 	Hot-fudge,	Coconut-creams,	Pure-cod-liver-oil
	 0 -> 	Pure-cod-liver-oil,	Hot-fudge,	Coconut-creams
	 0 -> 	Pure-cod-liver-oil,	Coconut-creams,	Hot-fudge
	 0 -> 	Coconut-creams,	Hot-fudge,	Pure-cod-liver-oil
	 0 -> 	Coconut-creams,	Pure-cod-liver-oil,	Hot-fudge
		 1 -> 	Pure-cod-liver-oil
		 1 -> 	Hot-fudge
		 1 -> 	Coconut-creams
		 1 -> 	Coconut-creams,	Hot-fudge
		 1 -> 	Coconut-creams,	Pure-cod-liver-oil
		 1 -> 	Hot-fudge,	Pure-cod-liver-oil
		 1 -> 	Hot-fudge,	Pure-cod-liver-oil,	Coconut-creams
		 1 -> 	Hot-fudge,	Coconut-creams,	Pure-cod-liver-oil
		 1 -> 	Pure-cod-liver-oil,	Hot-fudge,	Coconut-creams
		 1 -> 	Pure-cod-liver-oil,	Coconut-creams,	Hot-fudge
		 1 -> 	Coconut-creams

...

		 1 -> 	Lemongrass-paste,	Chicken-kievs,	Polenta
		 1 -> 	Lemongrass-paste,	Chicken-kievs,	Sussungsmittel
		 1 -> 	Lemongrass-paste,	Instant-porridge,	Chicken-kievs
		 1 -> 	Lemongrass-paste,	Instant-porridge,	Polenta
		 1 -> 	Lemongrass-paste,	Instant-porridge,	Sussungsmittel
		 1 -> 	Lemongrass-paste,	Polenta,	Chicken-kievs
		 1 -> 	Lemongrass-paste,	Polenta,	Instant-porridge
		 1 -> 	Lemongrass-paste,	Polenta,	Sussungsmittel
		 1 -> 	Lemongrass-paste,	Sussungsmittel,	Chicken-kievs
		 1 -> 	Lemongrass-paste,	Sussungsmittel,	Instant-porridge
		 1 -> 	Lemongrass-paste,	Sussungsmittel,	Polenta
		 1 -> 	Chicken-kievs,	Lemongrass-paste,	Instant-porridge
		 1 -> 	Chicken-kievs,	Lemongrass-paste,	Polenta
		 1 -> 	Chicken-kievs,	Lemongrass-paste,	Sussungsmittel
		 1 -> 	Chicken-kievs,	Instant-porridge,	Lemongrass-paste
		 1 -> 	Chicken-kievs,	Instant-porridge,	Polenta
		 1 -> 	Chicken-kievs,	Instant-porridge,	Sussungsmittel
		 1 -> 	Chicken-kievs,	Polenta,	Lemongrass-paste
		 1 -> 	Chicken-

	 0 -> 	Instant-porridge,	Lemongrass-paste,	Chicken-kievs,	Sussungsmittel
	 0 -> 	Instant-porridge,	Lemongrass-paste,	Polenta,	Chicken-kievs
	 0 -> 	Instant-porridge,	Lemongrass-paste,	Polenta,	Sussungsmittel
	 0 -> 	Instant-porridge,	Lemongrass-paste,	Sussungsmittel,	Chicken-kievs
	 0 -> 	Instant-porridge,	Lemongrass-paste,	Sussungsmittel,	Polenta
	 0 -> 	Instant-porridge,	Chicken-kievs,	Lemongrass-paste,	Polenta
	 0 -> 	Instant-porridge,	Chicken-kievs,	Lemongrass-paste,	Sussungsmittel
	 0 -> 	Instant-porridge,	Chicken-kievs,	Polenta,	Lemongrass-paste
	 0 -> 	Instant-porridge,	Chicken-kievs,	Polenta,	Sussungsmittel
	 0 -> 	Instant-porridge,	Chicken-kievs,	Sussungsmittel,	Lemongrass-paste
	 0 -> 	Instant-porridge,	Chicken-kievs,	Sussungsmittel,	Polenta
	 0 -> 	Instant-porridge,	Polenta,	Lemongrass-paste,	Chicken-kievs
	 0 -> 	Instant-porridge,	Polenta,	Lemongrass-paste,	Sussungsmittel
	 0 -> 	Instant-porridge,	Polenta,	Chicken-kievs,	Lemongrass-paste
	 0 -> 	Instant-porridge,	Polenta,	

				 3 -> 	Legumes-prepares
					 4 -> 	Jus-de-fruits
					 4 -> 	Legumes-prepares
	 0 -> 	Malt-drink
		 1 -> 	Legumes-prepares
				 3 -> 	Jus-de-fruits
	 0 -> 	Legumes-prepares
			 2 -> 	Jus-de-fruits

->  Sussungsmittel
	 0 -> 	Chicken-kievs
	 0 -> 	Polenta
	 0 -> 	Sussungsmittel
	 0 -> 	Lemongrass-paste
	 0 -> 	Almond-fingers
	 0 -> 	Instant-porridge
	 0 -> 	Chicken-kievs,	Lemongrass-paste
	 0 -> 	Instant-porridge,	Lemongrass-paste
	 0 -> 	Lemongrass-paste,	Sussungsmittel
	 0 -> 	Polenta,	Sussungsmittel
	 0 -> 	Chicken-kievs,	Instant-porridge
	 0 -> 	Instant-porridge,	Sussungsmittel
	 0 -> 	Chicken-kievs,	Polenta
	 0 -> 	Lemongrass-paste,	Polenta
	 0 -> 	Instant-porridge,	Polenta
	 0 -> 	Chicken-kievs,	Sussungsmittel
	 0 -> 	Lemongrass-paste,	Chicken-kievs,	Instant-porridge
	 0 -> 	Lemongrass-paste,	Chicken-kievs,	Polenta
	 0 -> 	Lemongrass-paste,	Chicken-kievs,	Sussungsmittel
	 0 -> 	Lemongrass-paste,	Instant-porridge,	Chicken-kievs
	 0 -> 	Lemongrass-paste,	Instant-porridge,	Polen

		 1 -> 	Sussungsmittel,	Lemongrass-paste,	Polenta,	Chicken-kievs
		 1 -> 	Sussungsmittel,	Lemongrass-paste,	Polenta,	Instant-porridge
		 1 -> 	Sussungsmittel,	Chicken-kievs,	Lemongrass-paste,	Instant-porridge
		 1 -> 	Sussungsmittel,	Chicken-kievs,	Lemongrass-paste,	Polenta
		 1 -> 	Sussungsmittel,	Chicken-kievs,	Instant-porridge,	Lemongrass-paste
		 1 -> 	Sussungsmittel,	Chicken-kievs,	Instant-porridge,	Polenta
		 1 -> 	Sussungsmittel,	Chicken-kievs,	Polenta,	Lemongrass-paste
		 1 -> 	Sussungsmittel,	Chicken-kievs,	Polenta,	Instant-porridge
		 1 -> 	Sussungsmittel,	Instant-porridge,	Lemongrass-paste,	Chicken-kievs
		 1 -> 	Sussungsmittel,	Instant-porridge,	Lemongrass-paste,	Polenta
		 1 -> 	Sussungsmittel,	Instant-porridge,	Chicken-kievs,	Lemongrass-paste
		 1 -> 	Sussungsmittel,	Instant-porridge,	Chicken-kievs,	Polenta
		 1 -> 	Sussungsmittel,	Instant-porridge,	Polenta,	Lemongrass-paste
		 1 -> 	Sussungsmittel,	Instant-porridge,	Polenta,	Chicken-kievs
		 1 -> 	Sussungsmittel,	Polent

KeyboardInterrupt: 

In [23]:
from copy import deepcopy
p2 = deepcopy(patterns)#####################################da eliminare alla fine

In [24]:
patterns = deepcopy(p2)#####################################da togliere alla fine
patNewLevel = []
for pattern in [p for p in patterns if p[1] != []]:
    l = [pattern[0][0],[]]
    for items in pattern[1]:
        level = items[0][0]
        item  = items[0][1]
        check = False
        for couple in l[1]:
            if couple[0] == level:
                couple[1].append(item)
                check = True
        if not check:
            l[1].append([level,[item]])
    patNewLevel.append(l)
patNewLevel = sorted(patNewLevel)

In [25]:
# Return the length of a model (in terms of depth levels)
def howManyLevels(pattern):
    return len(pattern[1])

#Return the length of a route starting from the passed order
def howManyOrders(route, order): #remaining orders after the one selected
    length = 0
    before  = False
    check   = False
    end     = False
    index = 0
    while (not end) & (index < len(routes)):
        if routes.RouteId[index] == route:
            before = True
            if routes.Order[index] > order:     
                length += 1
        else:
            before = False
            
        if before == True:
            if check == False:
                check = True
        else:
            if check == True:
                end = True
        index += 1
    return length

# Return the sorted levels of a pattern
def getLevels(pattern):
    return sorted(pattern[1])

# Return the orders inside a route
def getRoute(routeId):
    route = []
    before  = False
    check   = False
    end     = False
    i = 0
    while (not end) & (i < len(routes)):
        if routes.RouteId[i] == routeId:
            before = True
            route.append(routes.iloc[i])
        else:
            before = False
        if before == True:
            if check == False:
                check = True
        else:
            if check == True:
                end = True
        i += 1
    return route

# Return the index in the dataframe of a couple (route, order)
def getIndex(route, order):
    for index in range(0, len(routes)):
        if (routes.RouteId[index] == route) & (routes.Order[index] == order):
            return index
    return -1

In [ ]:
import time
a = time.time()
foundInRoute = {}
for r in range(0, max(routes.RouteId)):
    for trip in getRoute(r):
        for pattern in patNewLevel:
            # If in this trip we have the head of the pattern
            if pattern[0] in trip.Items:
                # Go ahead only if there are at least the same number of orders and levels of the pattern
                if howManyLevels(pattern) <= howManyOrders(trip.RouteId, trip.Order): 
                    for level in getLevels(pattern):  
                        for item in level[1]:
                            if set(item).intersection(set(routes.Items[getIndex(trip.RouteId, 
                                                                                trip.Order) 
                                                                       + level[0] 
                                                                       + 1])) == set(item):
                                if foundInRoute.get((trip.RouteId, 
                                                     trip.Order), 
                                                    "ORDER") == "ORDER":
                                    foundInRoute[(trip.RouteId, trip.Order)] = {level[0]: set((item,))}
                                else:
                                    if foundInRoute.get((trip.RouteId, 
                                                         trip.Order)).get(level[0], 
                                                                          "LEVEL") == "LEVEL":
                                        foundInRoute[(trip.RouteId, 
                                                      trip.Order)][level[0]] = set((item,))
                                    else:
                                        foundInRoute.get((trip.RouteId,
                                                          trip.Order)).get(level[0]).add(item)
print()
print(time.time()-a)
print()
foundInRoute